In [37]:
import matplotlib.pyplot as plt
import matplotlib.cm as cm
import networkx as nx
import csv

hist = []
files = ['../excel/dados_historicos_alunos_de_EngComputacaoCuritiba formados.csv',
         '../excel/dados_historicos_alunos_de_EngComputacaoCuritiba regulares.csv',
         '../excel/dados_historicos_alunos_de_EngComputacaoCuritiba trancados.csv',
         '../excel/dados_historicos_alunos_de_EngComputacaoCuritiba desistentes mudancas curso.csv'
         ]

# preenche as listas iniciais
for file in files:
    print(file)
    with open(file, 'r') as csvfile:   
        reader = csv.DictReader(csvfile, delimiter=';')
        for row in reader:
            hist.append(row)
print(len(hist))
print(hist[0])

../excel/dados_historicos_alunos_de_EngComputacaoCuritiba formados.csv
../excel/dados_historicos_alunos_de_EngComputacaoCuritiba regulares.csv
../excel/dados_historicos_alunos_de_EngComputacaoCuritiba trancados.csv
../excel/dados_historicos_alunos_de_EngComputacaoCuritiba desistentes mudancas curso.csv
76844
{'ID_ANONIMO': '13236', 'CR': '0,6826', 'PERIODO': '1', 'INGRESSO': '12/07/07', 'CODIGO': 'IF68E', 'ANO': '2012', 'NOTA': '8,2', 'CH': '60', 'SITUACAOALUNO': 'Formado'}


In [2]:
# função para verificar se um aluno teve seu ingresso antes ou depois de 2014
def beforeClasses(date):
    year = date.split('/')[2]
    if (int(year) < 14):
        return True
    return False

In [3]:
# Remove todos os alunos que ingressaram antes de 2014 
for i in range(len(hist)):
    if (i == len(hist)):
        break
    if (beforeClasses(hist[i]['INGRESSO'].split(" ")[0])):
        hist.pop(i)
        i = 0

# Remove todos dados de reprovações (matérias repetidas)
for i in range(len(hist)):
    for j in range(i, len(hist)):
        if (j == len(hist)):
            break
        if (hist[i]["ID_ANONIMO"] != hist[j]["ID_ANONIMO"]):
            break
        if (j < len(hist) and (i != j and (hist[i]["ID_ANONIMO"] == hist[j]["ID_ANONIMO"] and hist[i]["CODIGO"] == hist[j]["CODIGO"]))):
            hist.pop(j)
            j -= 5
len(hist)

# TODO: caso o aluno tenha reprovado em uma matéria, deve ser removido também. 
# Uma reprovação não conta para o sistema de recomendação

49188

In [4]:
G = nx.Graph()

# Adiciona todos os nós, que são os alunos
# Sem colocar nenhum aluno pré-2014
for line in hist:
    if (not beforeClasses(line['INGRESSO'].split(" ")[0])):
        if not G.has_node(line["ID_ANONIMO"]):
            G.add_node(line["ID_ANONIMO"])
G.nodes()

NodeView(('90729', '113853', '118844', '123664', '123676', '123677', '123686', '123688', '123736', '129034', '131006', '131014', '136341', '136730', '136731', '136736', '145077', '150873', '150878', '150887', '150892', '151217', '156158', '158257', '159067', '160836', '160839', '160852', '160855', '161216', '161223', '161226', '161228', '165431', '165432', '165685', '165892', '165894', '165895', '166050', '169043', '171740', '171745', '171746', '171749', '171750', '171751', '171754', '171755', '172044', '172045', '172046', '172207', '172208', '172248', '172307', '172974', '175962', '179385', '179393', '179397', '179408', '179624', '179652', '179819', '179822', '179823', '179944', '180984', '182856', '182913', '183413', '183414', '186021', '186024', '186036', '189048', '190493', '190494', '190495', '190499', '190508', '190615', '191284', '198372', '198543', '202261', '11357', '104342', '104372', '104768', '110307', '113861', '118817', '123657', '123682', '124800', '126813', '130359', '1

In [5]:
print(G.number_of_nodes())

901


In [6]:
# Verifica quais são as matérias obrigatórias, que não serão levadas em conta
optional = []
with open('../texts/optativas.txt', 'r') as f:   
    lines = f.readlines()
    for l in lines:
        optional.append(l.split(" ")[0])

print(optional)

['CSH30', 'CSV30', 'CSH42', 'CSI53', 'CSV40', 'CSR44', 'CSR41', 'CSR42', 'MA70C', 'CSB51', 'ED70T', 'CSB41', 'CSI41', 'DI84D', 'CSV45', 'CSR43', 'CSM44', 'CSM41', 'CSM43', 'ES70J', 'ES70B', 'CSM40', 'CSB53', 'ES70N', 'GE70F', 'CSA44', 'CSB54', 'CSH44', 'EEY41', 'ED70U', 'CSH43', 'CSE40', 'CSM30', 'CSI56', 'CSA45', 'FI70B', 'FI70D', 'CSA42', 'EL64B', 'CSV52', 'CSB52', 'CSD41', 'FI70A', 'CSD40', 'CSR53', 'CSG42', 'CSI58', 'CSI57', 'CSG48', 'CSV41', 'CSI51', 'CSW45', 'CSE43', 'CSI55', 'FCH7HB', 'CSR47', 'EEY44', 'CSH45', 'CSA41', 'EEC41', 'EL6CB', 'EEY43', 'CSR48', 'EEY42', 'EL6AE', 'CSH41', 'CSD52', 'EEY51', 'EEL51', 'CSI54', 'CSA43', 'CSW47', 'CSI31', 'IF6BV', 'CSR45', 'CSG44', 'FI70E', 'EL75H']


In [7]:
# Adiciona as arestas
with open('all_edges.txt', 'w') as f:
    for i in range(len(hist)):
        # o estudante deve estar no grafo
        if G.has_node(hist[i]["ID_ANONIMO"]):
            # a disciplina não pode ser obrigatória
            if (hist[i]["CODIGO"] in optional):
                for j in range(i, len(hist)):
                    # o estudante deve estar no grafo
                    if G.has_node(hist[j]["ID_ANONIMO"]):
                        # a disciplina não pode ser obrigatória
                        if (hist[j]["CODIGO"] in optional):
                            # os alunos deve ser diferentes
                            if (hist[i]["ID_ANONIMO"] != hist[j]["ID_ANONIMO"]):
                                # as matérias devem ser as mesmas
                                if (hist[i]["CODIGO"] == hist[j]["CODIGO"]):
                                    f.write(hist[i]["ID_ANONIMO"] + " - " + hist[j]["ID_ANONIMO"] + " : " + hist[j]["CODIGO"] + "\n")
                                    if (G.has_edge(hist[i]["ID_ANONIMO"], hist[j]["ID_ANONIMO"])):
                                        G[hist[i]["ID_ANONIMO"]][hist[j]["ID_ANONIMO"]]['weight'] += 1
                                    else:
                                        G.add_edge(hist[i]["ID_ANONIMO"], hist[j]["ID_ANONIMO"], weight = 1) 

In [8]:
# Remover as arestas com peso pequeno
edges_remove = []
for u, v, a in G.edges(data=True):
    if a["weight"] < 0:
        edges_remove.append([u, v])
G.remove_edges_from(edges_remove)

In [9]:
print(G.number_of_edges())

17852


In [10]:
# ordena os vértices por grau, para verificar os alunos com maior n de matérias em comum
degrees = sorted(G.degree, key=lambda x: x[1], reverse=True)
remove = [node for node, degree in dict(G.degree()).items() if degree == 0]
G.remove_nodes_from(remove)
G.number_of_nodes()

260

In [11]:
with open('node_degree_all.txt', 'w') as f:
    for degree in degrees:
        f.write(str(degree) + "\n")

In [12]:
# Escreve o arquivo gexf para visualização de grafos
nx.write_gexf(G, "grafo_caminho.gexf")

In [13]:
# ordena as arestas por peso, buscando assim quais os estudantes mais relacionadas
edges = sorted(G.edges(data=True), key=lambda edge: edge[2].get('weight', 1))
with open('edge_weights.txt', 'w') as f1:
    for edge in edges:
        f1.write(str(edge) + "\n")


In [14]:
import leidenalg as la
import igraph as ig
# Separa o grafo em comunidades
# O alg usado para isso é o Leinden, com a biblioteca LeidenAlg
# para isso, é preciso transformar o grafo do networkX para Igraph
H = ig.Graph.from_networkx(G)
H.is_weighted()

True

In [15]:
ws = []
for e in H.es():
  ws.append(e['weight'])

In [16]:
ig.plot(H)

In [17]:
# Agora roda a partição
partition = la.find_partition(H, la.ModularityVertexPartition, weights=H.es()[:]["weight"], n_iterations=50)
ig.plot(partition)

In [18]:
partition.membership

[1,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 2,
 0,
 2,
 1,
 2,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 2,
 1,
 1,
 1,
 2,
 1,
 1,
 1,
 0,
 2,
 1,
 0,
 1,
 0,
 0,
 2,
 0,
 1,
 1,
 2,
 1,
 0,
 2,
 1,
 0,
 2,
 0,
 2,
 2,
 2,
 0,
 0,
 0,
 0,
 2,
 1,
 2,
 0,
 2,
 2,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 2,
 2,
 2,
 0,
 1,
 2,
 1,
 1,
 1,
 0,
 2,
 1,
 0,
 2,
 2,
 0,
 0,
 1,
 1,
 0,
 0,
 2,
 1,
 1,
 0,
 2,
 1,
 0,
 1,
 1,
 0,
 0,
 0,
 0,
 0,
 2,
 0,
 0,
 1,
 2,
 2,
 0,
 0,
 2,
 2,
 2,
 2,
 0,
 2,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 2,
 0,
 2,
 1,
 2,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 2,
 0,
 0,
 0,
 0,
 2,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 0,
 2,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 0,
 0,
 1,
 1,
 1,
 1,
 2,
 1,
 2,
 1,
 1,
 0,
 1,
 2,
 0,
 0,
 1,
 1,
 1,
 1,
 1,
 2,
 1,
 1,
 2,
 1,
 2,
 1,
 2,
 1,
 1,
 2,
 0,
 1,
 1,
 2,
 1,
 1,
 2,
 1,
 2,
 2,
 1,
 1,
 2,
 0,
 2,
 2,
 2,
 2,
 0,
 2,
 1,
 1,
 1,
 1,
 2,
 1,
 1,
 1,
 2,
 1,
 1,
 2,
 2,
 0,


In [64]:
com_0 = [H.vs()[idx]["_nx_name"] for idx, com in enumerate(partition.membership) if com == 0]
com_1 = [H.vs()[idx]["_nx_name"] for idx, com in enumerate(partition.membership) if com == 1]
com_2 = [H.vs()[idx]["_nx_name"] for idx, com in enumerate(partition.membership) if com == 2]
com_3 = [H.vs()[idx]["_nx_name"] for idx, com in enumerate(partition.membership) if com == 3]

comunidades = []
for y in range(0,3):
    comunidades.append([H.vs()[idx]["_nx_name"] for idx, com in enumerate(partition.membership) if com == y])

print(comunidades)

[['118844', '123676', '123677', '123686', '123688', '131006', '131014', '136341', '136730', '136731', '136736', '145077', '150873', '150887', '169043', '171746', '171750', '171751', '171755', '172208', '172974', '179385', '179624', '179652', '179819', '179822', '182856', '183414', '186021', '186024', '186036', '189048', '190493', '190494', '190495', '190499', '190508', '190615', '202261', '123682', '130359', '136734', '137191', '157060', '160791', '161257', '166152', '171652', '171698', '172042', '172975', '175468', '175799', '176199', '179389', '179402', '185876', '186027', '186031', '186037', '190501', '190502', '190706', '193632', '193637', '202250', '202252', '202254', '202256', '202266', '202268', '202417', '202689', '202696', '202701', '206316', '208887', '212651', '212652', '212661', '212662', '212665', '212667', '212672', '212674', '212675', '213594', '213596', '229544', '124741', '190512', '202253', '130999', '136718', '145055', '161181', '165893', '171688', '195575', '198545'

In [51]:
# Pandas
import pandas as pd
# preenche as listas iniciais
dados = []
for file in files:
    print(file)
    with open(file, 'r') as csvfile:   
        dados.append(pd.read_csv(csvfile, delimiter=';'))

dados = pd.concat(dados)

../excel/dados_historicos_alunos_de_EngComputacaoCuritiba formados.csv
../excel/dados_historicos_alunos_de_EngComputacaoCuritiba regulares.csv
../excel/dados_historicos_alunos_de_EngComputacaoCuritiba trancados.csv
../excel/dados_historicos_alunos_de_EngComputacaoCuritiba desistentes mudancas curso.csv


In [52]:
dados

ID_ANONIMO      CR PERIODO  INGRESSO  CODIGO   ANO  PERIODO.1 NOTA  CH  \
0           13236  0,6826      10  12/07/07   IF68E  2012          1  8,2  60   
1           13236  0,6826      10  12/07/07   IF35J  2007          2    7  60   
2           13236  0,6826      10  12/07/07   MA33K  2007          2    0  60   
3           13236  0,6826      10  12/07/07  F2D070  2007          2  8,8  75   
4           13236  0,6826      10  12/07/07  E1D000  2007          2    0  30   
...           ...     ...     ...       ...     ...   ...        ...  ...  ..   
25004      255652       0       1  20/03/23  ICSD20  2023          1    0  45   
25005      255652       0       1  20/03/23  ICSF13  2023          1    0  90   
25006      255652       0       1  20/03/23  FIS7F1  2023          1    0  60   
25007      255652       0       1  20/03/23  MAT7GA  2023          1    0  60   
25008      255652       0       1  20/03/23  MAT7C1  2023          1    0  90   

      SITUACAOALUNO  
0           Formado  
1           Formado  
2           Formado  
3           Formado  
4           Formado  
...             ...  
25004    Desistente  
25005    Desistente  
25006    Desistente  
25007    Desistente  
25008    Desistente  

[76844 rows x 10 columns]

In [163]:
dados_filtrados = dados[dados.CODIGO.apply(lambda a: a in optional)]
dados_filtrados

ID_ANONIMO      CR PERIODO  INGRESSO CODIGO   ANO  PERIODO.1 NOTA  CH  \
36          13236  0,6826      10  12/07/07  CSA43  2016          1    3  60   
65          13236  0,6826      10  12/07/07  MA70C  2012          2  8,6  60   
332         51624  0,6161      10  03/08/09  CSH30  2017          2    6  45   
349         51624  0,6161      10  03/08/09  EL64B  2017          2  6,3  60   
394         51624  0,6161      10  03/08/09  CSR41  2017          2  8,1  60   
...           ...     ...     ...       ...    ...   ...        ...  ...  ..   
24947      250148  0,7231       4  21/07/22  FI70A  2022          2  7,5  60   
24948      250148  0,7231       4  21/07/22  MA70C  2022          2  7,3  60   
24949      250148  0,7231       4  21/07/22  FI70D  2022          2  7,3  30   
24950      250148  0,7231       4  21/07/22  FI70E  2022          2  7,3  45   
24951      250148  0,7231       4  21/07/22  CSM43  2022          2    9  60   

      SITUACAOALUNO  
36          Formado  
65          Formado  
332         Formado  
349         Formado  
394         Formado  
...             ...  
24947    Desistente  
24948    Desistente  
24949    Desistente  
24950    Desistente  
24951    Desistente  

[2632 rows x 10 columns]

In [161]:
print(comunidades)

[['118844', '123676', '123677', '123686', '123688', '131006', '131014', '136341', '136730', '136731', '136736', '145077', '150873', '150887', '169043', '171746', '171750', '171751', '171755', '172208', '172974', '179385', '179624', '179652', '179819', '179822', '182856', '183414', '186021', '186024', '186036', '189048', '190493', '190494', '190495', '190499', '190508', '190615', '202261', '123682', '130359', '136734', '137191', '157060', '160791', '161257', '166152', '171652', '171698', '172042', '172975', '175468', '175799', '176199', '179389', '179402', '185876', '186027', '186031', '186037', '190501', '190502', '190706', '193632', '193637', '202250', '202252', '202254', '202256', '202266', '202268', '202417', '202689', '202696', '202701', '206316', '208887', '212651', '212652', '212661', '212662', '212665', '212667', '212672', '212674', '212675', '213594', '213596', '229544', '124741', '190512', '202253', '130999', '136718', '145055', '161181', '165893', '171688', '195575', '198545'

In [ ]:
from collections import Counter

disciplinas_comunidades = []

# Pega as disciplinas de cada comunidade
for idx, comunidade in enumerate(comunidades):
    disciplinas_comunidades.append(pd.DataFrame())
    for id in comunidade:
        disciplinas_comunidades[idx] = pd.concat([disciplinas_comunidades[idx],
                   (dados_filtrados[dados_filtrados.ID_ANONIMO.apply(lambda a: a == int(id))])
                  ])
        pass

# Pega as disciplinas mais populares em cada comunidade
for comunidade in disciplinas_comunidades:
    print("Comunidade 1: " + str(Counter(comunidade.CODIGO)))

In [158]:
dados_filtrados[dados_filtrados.ID_ANONIMO.apply(lambda a: a == int(id))]

ID_ANONIMO      CR PERIODO  INGRESSO CODIGO   ANO  PERIODO.1 NOTA  CH  \
23856      208880  0,7152       5  06/08/18  CSM40  2021          2  8,3  60   
23857      208880  0,7152       5  06/08/18  CSH30  2021          2  7,9  45   

        SITUACAOALUNO  
23856  Mudou de Curso  
23857  Mudou de Curso

In [156]:
disciplinas_comunidades

[Empty DataFrame
 Columns: []
 Index: [],
 Empty DataFrame
 Columns: []
 Index: [],
 Empty DataFrame
 Columns: []
 Index: []]